# Prism example

This tutorial demonstrates how to open an existing Speos file, run
the simulation and open the result. After that it explains how to
edit the File and adjust Parameters of the sensor.

## Prerequisites

### Perform imports

In [1]:
import os
from pathlib import Path

from ansys.speos.core import Project, Speos
from ansys.speos.core.launcher import launch_local_speos_rpc_server
from ansys.speos.core.sensor import SensorIrradiance
from ansys.speos.core.simulation import SimulationDirect


### Define constants

The constants help ensure consistency and avoid repetition throughout the example.

In [2]:
HOSTNAME = "localhost"
GRPC_PORT = 50098  # Be sure the Speos GRPC Server has been started on this port.
USE_DOCKER = True  # Set to False if you're running this example locally as a Notebook.

## Model Setup

### Load assets
The assets used to run this example are available in the
[PySpeos repository](https://github.com/ansys/pyspeos/) on GitHub.

> **Note:** Make sure you
> have downloaded simulation assets and set ``assets_data_path``
> to point to the assets folder.

In [3]:
if USE_DOCKER:  # Running on the remote server.
    assets_data_path = Path("/app") / "assets"
else:
    assets_data_path = Path("/path/to/your/download/assets/directory")

### Start/Connect to Speos RPC Server
This Python client connects to a server where the Speos engine
is running as a service. In this example, the server and
client are the same machine. The launch_local_speos_rpc_method can
be used to start a local instance of the service.

In [4]:
if USE_DOCKER:
    speos = Speos(host=HOSTNAME, port=GRPC_PORT)
else:
    speos = launch_local_speos_rpc_server(port=GRPC_PORT)

## Create project

Load a project from .speos file.

In [5]:
p = Project(speos=speos, path=str(assets_data_path / "Prism.speos" / "Prism.speos"))
print(p)

{
    "name": "Prism",
    "description": "From /app/assets/Prism.speos/Prism.speos",
    "part_guid": "902e01b3-6c1e-47a4-a266-91c286d6e397",
    "sources": [
        {
            "name": "Surface.1:7758",
            "metadata": {
                "UniqueId": "a2e740fa-389d-4adf-829a-8171ee191ee6"
            },
            "source_guid": "68998f7f-aa95-4961-b0e4-39dfe7ebff21",
            "description": "",
            "source": {
                "name": "Surface.1:7758",
                "surface": {
                    "radiant_flux": {
                        "radiant_value": 8.346636625511586
                    },
                    "intensity_guid": "646223f8-4ab6-4515-8cb7-82c05b12545c",
                    "exitance_constant": {
                        "geo_paths": [
                            {
                                "geo_path": "SourceBody:1801986974/face.1:544289899",
                                "reverse_normal": false
                            }
         

## Preview
This preview method allows you to preview the content of the Speos solver
file.

In [6]:
p.preview()

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

## Retrieve the simulation feature and open result

Run the simulation

In [7]:
sim_features = p.find(name="Prism", feature_type=SimulationDirect)
sim = sim_features[0]
sim.compute_CPU()

[upload_response {
  info {
    uri: "cf49eb9f-887c-4b3a-a801-b339f9134ad1"
    file_name: "Prism.Irradiance.1.xmp"
    file_size: 1569108
  }
  upload_duration {
    nanos: 3644368
  }
}
, upload_response {
  info {
    uri: "2a33e866-d0c1-4afc-938a-c6ed95501a8f"
    file_name: "Prism.html"
    file_size: 65534
  }
  upload_duration {
    nanos: 302355
  }
}
]

Use the open_result_image method to review the result

In [8]:
if os.name == "nt":
    from ansys.speos.core.workflow.open_result import open_result_image

    open_result_image(simulation_feature=sim, result_name="Prism.Irradiance.1.xmp")

## Work with sensor

Retrieve the sensor feature.

Modify the sensor setting, e.g. set the spectral type, etc.

In [9]:
irr_features = p.find(name=".*", name_regex=True, feature_type=SensorIrradiance)
irr = irr_features[0]
irr.set_type_spectral().set_wavelengths_range().set_start(500).set_end(600).set_sampling(11)
irr.commit()

## Re-run the simulation with new sensor definition.

In [10]:
sim.compute_CPU()
if os.name == "nt":
    open_result_image(simulation_feature=sim, result_name="Prism.Irradiance.1.xmp")

In [11]:
speos.close()

True